In [289]:
import sys
sys.path.append('../cfq')

from itertools import *
import pickle
import numpy as np
from data import RaggedArray, CFQDataset

np.set_printoptions(linewidth=150)

In [290]:
input_dir = '/work/yu_gai/cfq/data/cfq'

In [291]:
df = sqlCtx.read.parquet(f'/data/yu_gai/cfq/dataset.parquet/').sort('index').persist()
question = df.rdd.map(lambda r: r['questionPatternModEntities']).collect()
template = df.rdd.map(lambda r: r['questionTemplate']).collect()
sparql = df.rdd.map(lambda r: r['sparqlPatternModEntities']).collect()

In [292]:
dat = np.load(f'{input_dir}/data.npz')
idx = np.load(f'{input_dir}/splits/mcd3.npz')['testIdxs']
tok_vocab = idx2tok, _ = pickle.load(open(f'{input_dir}/tok-vocab.pickle', 'rb'))
tag_vocab = idx2tag, _ = pickle.load(open(f'{input_dir}/tag-vocab.pickle', 'rb'))
typ_vocab = idx2typ, _ = pickle.load(open(f'{input_dir}/typ-vocab.pickle', 'rb'))
dataset = CFQDataset(idx, dat, tok_vocab, tag_vocab, typ_vocab)
getitem = lambda key: dataset[np.where(idx == key)[0].item()]

In [286]:
dataset = CFQDataset(np.arange(len(dat)), dat, tok_vocab, tag_vocab, typ_vocab)

In [287]:
for d in dataset:
    pass

In [288]:
len(dataset)

13

In [293]:
out = np.load(f'/data/yu_gai/cfq/None_122820_142022/test_dict.npz')

In [294]:
n = np.array([getitem(index)['n'] for index in out['index']])
m = n * n
indptr = np.hstack([np.zeros(1), m.cumsum()]).astype(int)

In [295]:
def pos_typ(mem, n_mem, src, dst, typ):
    mem = RaggedArray(mem, np.cumsum(np.hstack([[0], n_mem])))
    i, j = np.where(typ)
    rels = []
    for u, t, v in zip(src[i], j, dst[i]):
        for x, y in product(mem[u], mem[v]):
            rels.append(f'{idx2tok[y]} {idx2typ[t]} {idx2tok[x]}')
    print(*sorted(rels), sep='\n')

In [298]:
for em, index, start, end in islice(zip(out['em'], out['index'], indptr[:-1], indptr[1:]), 10000):
    if not em and not question[index].startswith('Did'):
        print(question[index])
        print()
        isrel = lambda r: all(s not in r for s in ['!=', ' a ', 'ns:people.person.gender', 'ns:people.person.nationality'])
        print(*sorted(filter(isrel, sparql[index].split('\n')[1 : -1])), sep='\n')
        
        dat = getitem(index)
        templ = ' '.join([idx2tag[idx] for idx in dat['seq']])
        print(templ, templ in templ_train)
        src, dst = dat['src'], dat['dst']
        typ_true = out['typ_true'][start : end]
        typ_pred = out['typ_pred'][start : end]
#         print(src, dst)
#         print(typ_true.astype(int))
#         print(typ_pred.astype(int))
        
        print('*' * 75)
        pos_typ(dat['mem'], dat['n_mem'], src, dst, typ_true)
        
        print('*' * 75)
        pos_typ(dat['mem'], dat['n_mem'], src, dst, typ_pred)
        
        print('*' * 75)

Was M0 's actor M1 's parent and spouse

?x0 ns:film.actor.film/ns:film.performance.character M0 .
?x0 ns:people.person.children|ns:fictional_universe.fictional_character.children|ns:organization.organization.child/ns:organization.organization_relationship.child M1 .
?x0 ns:people.person.spouse_s/ns:people.marriage.spouse|ns:fictional_universe.fictional_character.married_to/ns:fictional_universe.marriage_of_fictional_characters.spouses M1 .
Was [entity] 's [ROLE_SIMPLE] [entity] 's [ROLE_SIMPLE] {SEP} ?x0 {NIL} False
***************************************************************************
?x0 ns:film.actor.film/ns:film.performance.character M0
?x0 ns:people.person.children|ns:fictional_universe.fictional_character.children|ns:organization.organization.child/ns:organization.organization_relationship.child M1
?x0 ns:people.person.spouse_s/ns:people.marriage.spouse|ns:fictional_universe.fictional_character.married_to/ns:fictional_universe.marriage_of_fictional_characters.spouses M1
***

***************************************************************************
?x0 ns:film.director.film M2
?x0 ns:people.person.employment_history/ns:business.employment_tenure.company M0
***************************************************************************
?x0 ns:film.director.film M2
***************************************************************************
Was M1 's French star M2 's spouse

?x0 ns:film.actor.film/ns:film.performance.film M1 .
?x0 ns:people.person.spouse_s/ns:people.marriage.spouse|ns:fictional_universe.fictional_character.married_to/ns:fictional_universe.marriage_of_fictional_characters.spouses M2 .
Was [entity] 's [ADJECTIVE_SIMPLE] [ROLE_SIMPLE] [entity] 's [ROLE_SIMPLE] {SEP} ?x0 {NIL} False
***************************************************************************
?x0 ns:film.actor.film/ns:film.performance.film M1
?x0 ns:people.person.spouse_s/ns:people.marriage.spouse|ns:fictional_universe.fictional_character.married_to/ns:fictional_universe.marriage_of_

***************************************************************************
?x0 ^ns:people.person.nationality M1
?x0 ns:people.person.children|ns:fictional_universe.fictional_character.children|ns:organization.organization.child/ns:organization.organization_relationship.child M0
***************************************************************************
?x0 ^ns:people.person.nationality M1
***************************************************************************
Was M1 's art director a screenwriter

?x0 ns:film.film_art_director.films_art_directed M1
Was [entity] 's [ROLE_SIMPLE] a [NP_SIMPLE] {SEP} ?x0 {NIL} False
***************************************************************************
?x0 ns:film.film_art_director.films_art_directed M1
***************************************************************************

***************************************************************************
Was M1 's cinematographer a cinematographer 's Italian child

?x0 ns:film.cinematographer.fil

Was [entity] 's [ROLE_SIMPLE] [VP_SIMPLE] by , [VP_SIMPLE] by , [VP_SIMPLE] by , and [VP_SIMPLE] by [entity] {SEP} ?x0 {NIL} False
***************************************************************************
?x0 ns:film.film.directed_by M1
?x0 ns:film.film.directed_by M2
?x0 ns:film.film.edited_by M1
?x0 ns:film.film.edited_by M2
?x0 ns:film.film.produced_by|ns:film.film.production_companies M1
?x0 ns:film.film.produced_by|ns:film.film.production_companies M2
?x0 ns:film.film.sequel M0
?x0 ns:film.film.written_by M1
?x0 ns:film.film.written_by M2
***************************************************************************
?x0 ns:film.film.sequel M0
***************************************************************************
Was M0 's prequel executive produced by and written by a screenwriter

?x0 ns:film.film.executive_produced_by ?x1 .
?x0 ns:film.film.sequel M0 .
?x0 ns:film.film.written_by ?x1 .
Was [entity] 's [ROLE_SIMPLE] [VP_SIMPLE] by and [VP_SIMPLE] by a [NP_SIMPLE] {SEP} ?x0 ?x

?x0 ns:film.film.edited_by M4
?x0 ns:film.film.sequel M0
?x0 ns:film.film.written_by M1
?x0 ns:film.film.written_by M2
?x0 ns:film.film.written_by M3
?x0 ns:film.film.written_by M4
***************************************************************************
?x0 ns:film.film.sequel M0
***************************************************************************
Was M0 's prequel written by M1 and M2 , produced by M6 , and written by M3 , M4 , and M5

?x0 ns:film.film.produced_by|ns:film.film.production_companies M6 .
?x0 ns:film.film.sequel M0 .
?x0 ns:film.film.written_by M1 .
?x0 ns:film.film.written_by M2 .
?x0 ns:film.film.written_by M3 .
?x0 ns:film.film.written_by M4 .
?x0 ns:film.film.written_by M5
Was [entity] 's [ROLE_SIMPLE] [VP_SIMPLE] by [entity] , [VP_SIMPLE] by [entity] , and [VP_SIMPLE] by [entity] {SEP} ?x0 {NIL} False
***************************************************************************
?x0 ns:film.film.produced_by|ns:film.film.production_companies M6
?x0 ns:film.fil

...

***************************************************************************
?x0 ns:film.actor.film/ns:film.performance.film M0
?x0 ns:people.person.parents|ns:fictional_universe.fictional_character.parents|ns:organization.organization.parent/ns:organization.organization_relationship.parent ?x1
***************************************************************************
?x0 ns:people.person.parents|ns:fictional_universe.fictional_character.parents|ns:organization.organization.parent/ns:organization.organization_relationship.parent ?x1
***************************************************************************
What star of M1 was M2 's French spouse

?x0 ns:film.actor.film/ns:film.performance.film M1 .
?x0 ns:people.person.spouse_s/ns:people.marriage.spouse|ns:fictional_universe.fictional_character.married_to/ns:fictional_universe.marriage_of_fictional_characters.spouses M2 .
What [ROLE_SIMPLE] of [entity] was [entity] 's [ADJECTIVE_SIMPLE] [ROLE_SIMPLE] {SEP} ?x0 {NIL} True
*************

***************************************************************************
?x0 ns:film.actor.film/ns:film.performance.film M0
?x0 ns:film.producer.films_executive_produced M0
?x0 ns:film.producer.film|ns:film.production_company.films M0
?x0 ns:organization.organization_founder.organizations_founded M1
?x0 ns:organization.organization_founder.organizations_founded M2
?x0 ns:organization.organization_founder.organizations_founded M3
?x0 ns:organization.organization_founder.organizations_founded M4
?x0 ns:organization.organization_founder.organizations_founded M5
***************************************************************************
?x0 ns:organization.organization_founder.organizations_founded M1
?x0 ns:organization.organization_founder.organizations_founded M2
?x0 ns:organization.organization_founder.organizations_founded M3
?x0 ns:organization.organization_founder.organizations_founded M4
?x0 ns:organization.organization_founder.organizations_founded M5
**************************

What was a [NP_SIMPLE] whose [ROLE_SIMPLE] was [VP_SIMPLE] by , [VP_SIMPLE] , was [VP_SIMPLE] by , and was [VP_SIMPLE] by [entity] {SEP} ?x0 ?x1 {NIL} False
***************************************************************************
?x0 ns:film.film.sequel ?x1
?x1 ns:film.film.edited_by M1
?x1 ns:film.film.produced_by|ns:film.film.production_companies M1
?x1 ns:film.film.starring/ns:film.performance.actor M1
?x1 ns:film.film.written_by M1
***************************************************************************
?x0 ns:film.film.prequel ?x1
?x1 ns:film.film.produced_by|ns:film.film.production_companies M1
?x1 ns:film.film.starring/ns:film.performance.actor M1
***************************************************************************
What was a film whose sequel was executive produced by , edited by , written by , and directed by M1

?x0 ns:film.film.sequel ?x1 .
?x1 ns:film.film.directed_by M1 .
?x1 ns:film.film.edited_by M1 .
?x1 ns:film.film.executive_produced_by M1 .
?x1 ns:film.f

***************************************************************************
?x0 ns:film.film.directed_by M0
?x0 ns:film.film.directed_by M1
?x0 ns:film.film.directed_by M2
?x0 ns:film.film.directed_by M3
?x0 ns:film.film.directed_by M4
?x0 ns:film.film.edited_by M0
?x0 ns:film.film.edited_by M1
?x0 ns:film.film.edited_by M2
?x0 ns:film.film.edited_by M3
?x0 ns:film.film.edited_by M4
?x0 ns:film.film.produced_by|ns:film.film.production_companies M0
?x0 ns:film.film.produced_by|ns:film.film.production_companies M1
?x0 ns:film.film.produced_by|ns:film.film.production_companies M2
?x0 ns:film.film.produced_by|ns:film.film.production_companies M3
?x0 ns:film.film.produced_by|ns:film.film.production_companies M4
?x0 ns:film.film.written_by M0
?x0 ns:film.film.written_by M1
?x0 ns:film.film.written_by M2
?x0 ns:film.film.written_by M3
?x0 ns:film.film.written_by M4
***************************************************************************
?x0 ns:film.film.directed_by M0
?x0 ns:film.film.dire

***************************************************************************
?x0 ns:film.film.directed_by M0
?x0 ns:film.film.directed_by M1
?x0 ns:film.film.directed_by M2
?x0 ns:film.film.edited_by M0
?x0 ns:film.film.edited_by M1
?x0 ns:film.film.edited_by M2
?x0 ns:film.film.written_by M0
?x0 ns:film.film.written_by M1
?x0 ns:film.film.written_by M2
***************************************************************************
?x0 ns:film.film.directed_by M0
?x0 ns:film.film.directed_by M1
?x0 ns:film.film.directed_by M2
?x0 ns:film.film.edited_by M0
?x0 ns:film.film.edited_by M1
?x0 ns:film.film.edited_by M2
***************************************************************************
What was edited by , written by , and executive produced by M0 , M1 , and M2

?x0 ns:film.film.edited_by M0 .
?x0 ns:film.film.edited_by M1 .
?x0 ns:film.film.edited_by M2 .
?x0 ns:film.film.executive_produced_by M0 .
?x0 ns:film.film.executive_produced_by M1 .
?x0 ns:film.film.executive_produced_by M2 .
?

In [254]:
[templ for templ in templ_train if templ.startswith("Did a [ADJECTIVE_SIMPLE]")]

[]

In [168]:
ts = {' '.join([idx2tag[idx] for idx in getitem(index)['seq']]) for em, index in zip(out['em'], out['index']) if not em}

In [144]:
idx_train

array([166986, 239216, 177275, ..., 183022, 185019, 139419])

In [217]:
idx_train = np.load(f'{input_dir}/splits/mcd3.npz')['trainIdxs']
ds_train = CFQDataset(idx_train, dat, tok_vocab, tag_vocab, typ_vocab)
get_train = lambda key: ds_train[np.where(idx_train == key)[0].item()]
templ_train = {' '.join([idx2tag[idx] for idx in get_train(index)['seq']]) for index in idx_train}

In [218]:
idx_test = np.load(f'{input_dir}/splits/mcd3.npz')['testIdxs']
ds_test = CFQDataset(idx_test, dat, tok_vocab, tag_vocab, typ_vocab)
get_test = lambda key: ds_test[np.where(idx_test == key)[0].item()]
templ_test = {' '.join([idx2tag[idx] for idx in get_test(index)['seq']]) for index in idx_test}

In [219]:
both = templ_train.intersection(templ_test)
print(len(templ_train), len(templ_test), len(both))
list(islice(both, 10))

9148 1058 210


["Who was a [NP_SIMPLE] 's [ROLE_SIMPLE] {SEP} ?x0 ?x1 {NIL}",
 'Which [ADJECTIVE_SIMPLE] [NP_SIMPLE] was [VP_SIMPLE] by [entity] and was [VP_SIMPLE] by [entity] {SEP} ?x0 {NIL}',
 'Which [ROLE_SIMPLE] of a [NP_SIMPLE] was [VP_SIMPLE] by [entity] {SEP} ?x0 ?x1 {NIL}',
 'What did [entity] [VP_SIMPLE] and [entity] [VP_SIMPLE] {SEP} ?x0 {NIL}',
 'Which [NP_SIMPLE] was [VP_SIMPLE] by and [VP_SIMPLE] by [entity] {SEP} ?x0 {NIL}',
 "Which [ROLE_SIMPLE] of [entity] was [entity] 's [ROLE_SIMPLE] {SEP} ?x0 {NIL}",
 "Which [NP_SIMPLE] was a [NP_SIMPLE] 's [ROLE_SIMPLE] {SEP} ?x0 ?x1 {NIL}",
 'What [ADJECTIVE_SIMPLE] [NP_SIMPLE] was a [ROLE_SIMPLE] of [entity] {SEP} ?x0 {NIL}',
 "What [ROLE_SIMPLE] of [entity] was [entity] 's [ROLE_SIMPLE] {SEP} ?x0 {NIL}",
 'Which [ROLE_SIMPLE] of [entity] [VP_SIMPLE] [entity] {SEP} ?x0 {NIL}']

In [268]:
import re
from operator import *

In [271]:
def n_var(r):
    return len(set(re.findall(r'\?x\d', r['sparqlPatternModEntities'])))

def n(r):
    return sum(1 for tok in r['questionTemplate'].split(' ') if tok in ['[NP_SIMPLE]', '[ROLE_SIMPLE]', 'Who'])

# n_var(df.rdd.take(1)[0])
# n(df.rdd.take(1)[0])
df.rdd.map(lambda r: n_var(r) == n(r)).reduce(add)

115974

In [273]:
df.rdd.filter(lambda r: n_var(r) != n(r)).map(lambda r: r['questionTemplate']).take(10)

["Did [entity] 's [ROLE_SIMPLE] , [ROLE_SIMPLE] , [ROLE_SIMPLE] , and [ROLE_SIMPLE] [VP_SIMPLE] , [VP_SIMPLE] , and [VP_SIMPLE] [entity]",
 "Did [entity] 's [ROLE_SIMPLE] , [ROLE_SIMPLE] , [ROLE_SIMPLE] , [ROLE_SIMPLE] , and [ROLE_SIMPLE] [VP_SIMPLE] and [VP_SIMPLE] [entity]",
 "Did [entity] 's [ROLE_SIMPLE] and [ROLE_SIMPLE] [VP_SIMPLE] , [VP_SIMPLE] , and [VP_SIMPLE] [entity] , [entity] , and [entity]",
 "Did [entity] 's [ROLE_SIMPLE] , [ROLE_SIMPLE] , [ROLE_SIMPLE] , [ROLE_SIMPLE] , and [ROLE_SIMPLE] [VP_SIMPLE] and [VP_SIMPLE] [entity]",
 "Did [entity] 's [ROLE_SIMPLE] , [ROLE_SIMPLE] , [ROLE_SIMPLE] , and [ROLE_SIMPLE] [VP_SIMPLE] , [VP_SIMPLE] , [VP_SIMPLE] , and [VP_SIMPLE] [entity]",
 "Did [entity] 's [ROLE_SIMPLE] 's [ROLE_SIMPLE] , [ROLE_SIMPLE] , and [ROLE_SIMPLE] [VP_SIMPLE] [entity] and [entity] and [VP_SIMPLE] a [NP_SIMPLE] 's [ROLE_SIMPLE]",
 "Did [entity] [VP_SIMPLE] [entity] 's [ROLE_SIMPLE] , [VP_SIMPLE] a [ROLE_SIMPLE] and [ROLE_SIMPLE] of [entity] and [entity] , and

In [ ]:
df.rdd.map(lambda r: r['questionTemplate']).filter(lambda r: r.startswith(''))

In [270]:
df.count()

239357

In [261]:
print(df.rdd.map(lambda r: r['sparqlPatternModEntities']).take(1)[0])

SELECT count(*) WHERE {
?x0 ns:film.actor.film/ns:film.performance.character M1 .
?x0 ns:film.editor.film M0 .
?x0 ns:film.producer.film|ns:film.production_company.films M0 .
?x0 ns:people.person.gender ns:m.02zsn
}


In [255]:
df.columns

['complexityMeasures',
 'expectedResponse',
 'expectedResponseWithMids',
 'index',
 'question',
 'questionPatternModEntities',
 'questionTemplate',
 'questionWithBrackets',
 'questionWithMids',
 'ruleIds',
 'ruleTree',
 'sparql',
 'sparqlPattern',
 'sparqlPatternModEntities']

In [220]:
sum(1 for index in idx_test if ' '.join([idx2tag[idx] for idx in get_test(index)['seq']]) in both)

3081

In [247]:
[x for x in templ_train if x.startswith("Was [entity] 's")]

["Was [entity] 's [ROLE_SIMPLE] 's [ADJECTIVE_SIMPLE] [ROLE_SIMPLE] [entity] {SEP} ?x0 {NIL}",
 "Was [entity] 's [ADJECTIVE_SIMPLE] [ADJECTIVE_SIMPLE] [ROLE_SIMPLE] 's [ADJECTIVE_SIMPLE] [ADJECTIVE_SIMPLE] [ROLE_SIMPLE] [entity] {SEP} ?x0 {NIL}",
 "Was [entity] 's [ADJECTIVE_SIMPLE] [ROLE_SIMPLE] 's [ROLE_SIMPLE] [entity] {SEP} ?x0 {NIL}",
 "Was [entity] 's [ROLE_SIMPLE] 's [ROLE_SIMPLE] 's [ADJECTIVE_SIMPLE] [ROLE_SIMPLE] 's [ROLE_SIMPLE] [entity] {SEP} ?x0 ?x1 ?x2 {NIL}",
 "Was [entity] 's [ROLE_SIMPLE] 's [ADJECTIVE_SIMPLE] [ADJECTIVE_SIMPLE] [ADJECTIVE_SIMPLE] [ROLE_SIMPLE] [entity] {SEP} ?x0 {NIL}",
 "Was [entity] 's [ADJECTIVE_SIMPLE] [ROLE_SIMPLE] 's [ROLE_SIMPLE] 's [ROLE_SIMPLE] 's [ROLE_SIMPLE] [entity] {SEP} ?x0 ?x1 ?x2 {NIL}",
 "Was [entity] 's [ROLE_SIMPLE] 's [ADJECTIVE_SIMPLE] [ROLE_SIMPLE] 's [ROLE_SIMPLE] [entity] {SEP} ?x0 ?x1 {NIL}",
 "Was [entity] 's [ROLE_SIMPLE] 's [ROLE_SIMPLE] 's [ADJECTIVE_SIMPLE] [ROLE_SIMPLE] [entity] {SEP} ?x0 ?x1 {NIL}",
 "Was [entity] 's [

In [249]:
[x for x in templ_train if "a [NP_SIMPLE]" in x]

["Who was [VP_SIMPLE] by [entity] 's [ROLE_SIMPLE] and [VP_SIMPLE] by a [ROLE_SIMPLE] of a [NP_SIMPLE] {SEP} ?x0 ?x1 ?x2 ?x3 {NIL}",
 'What was [VP_SIMPLE] by , [VP_SIMPLE] by , [VP_SIMPLE] by , [VP_SIMPLE] by , and [VP_SIMPLE] by a [NP_SIMPLE] that [VP_SIMPLE] [entity] {SEP} ?x0 ?x1 {NIL}',
 'What was [VP_SIMPLE] by a [NP_SIMPLE] that [entity] was [VP_SIMPLE] by and [VP_SIMPLE] by and [VP_SIMPLE] by [entity] {SEP} ?x0 ?x1 {NIL}',
 'Which [NP_SIMPLE] [VP_SIMPLE] a [NP_SIMPLE] that [entity] was [VP_SIMPLE] by and [entity] [VP_SIMPLE] [entity] {SEP} ?x0 ?x1 {NIL}',
 'Did [entity] [VP_SIMPLE] [entity] , [VP_SIMPLE] a [ADJECTIVE_SIMPLE] [ROLE_SIMPLE] of [entity] , and [VP_SIMPLE] a [NP_SIMPLE] {SEP} ?x0 ?x1 {NIL}',
 "Was [entity] a [NP_SIMPLE] 's [ROLE_SIMPLE] 's [ROLE_SIMPLE] 's [ADJECTIVE_SIMPLE] [ROLE_SIMPLE] {SEP} ?x0 ?x1 ?x2 {NIL}",
 'Who was [VP_SIMPLE] by a [NP_SIMPLE] and was [VP_SIMPLE] by a [ROLE_SIMPLE] of a [ROLE_SIMPLE] of [entity] {SEP} ?x0 ?x1 ?x2 ?x3 {NIL}',
 'What [NP_SIMP

In [241]:
templ_test.difference(templ_train)

{"Did [entity] 's [ADJECTIVE_SIMPLE] [ADJECTIVE_SIMPLE] [ADJECTIVE_SIMPLE] [ROLE_SIMPLE] [VP_SIMPLE] [entity] and [VP_SIMPLE] [entity] {SEP} ?x0 {NIL}",
 "Did [entity] 's [ADJECTIVE_SIMPLE] [ADJECTIVE_SIMPLE] [ROLE_SIMPLE] [VP_SIMPLE] [entity] and [VP_SIMPLE] [entity] {SEP} ?x0 {NIL}",
 "Did [entity] 's [ADJECTIVE_SIMPLE] [ADJECTIVE_SIMPLE] [ROLE_SIMPLE] [VP_SIMPLE] [entity] and [VP_SIMPLE] a [NP_SIMPLE] {SEP} ?x0 ?x1 {NIL}",
 "Did [entity] 's [ADJECTIVE_SIMPLE] [ADJECTIVE_SIMPLE] [ROLE_SIMPLE] [VP_SIMPLE] [entity] {SEP} ?x0 {NIL}",
 "Did [entity] 's [ADJECTIVE_SIMPLE] [ADJECTIVE_SIMPLE] [ROLE_SIMPLE] [VP_SIMPLE] a [NP_SIMPLE] {SEP} ?x0 ?x1 {NIL}",
 "Did [entity] 's [ADJECTIVE_SIMPLE] [ROLE_SIMPLE] [VP_SIMPLE] [entity] , [VP_SIMPLE] [entity] , and [VP_SIMPLE] [entity] {SEP} ?x0 {NIL}",
 "Did [entity] 's [ADJECTIVE_SIMPLE] [ROLE_SIMPLE] [VP_SIMPLE] [entity] , [VP_SIMPLE] a [NP_SIMPLE] , and [VP_SIMPLE] [entity] {SEP} ?x0 ?x1 {NIL}",
 "Did [entity] 's [ADJECTIVE_SIMPLE] [ROLE_SIMPLE] [VP

In [243]:
set.difference?